In [3]:
# prob
import numpy as np


In [4]:
class GridWorld:
    def __init__(self,step_cost) :
        self.row = 5
        self.column = 5
        self.i = 4
        self.j = 0
        self.config(step_cost)

    def config(self,step_cost):
        reward = {}

        for p in range(self.row):
            for q in range(self.column):
                if p==0 and q==4:
                    reward[(p,q)] = 1
                elif p==1 and q==4:
                    reward[(p,q)] = -1
                elif p==2 and q==1:
                    reward[(p,q)] = -10
                elif p==3 and q==3:
                    reward[(p,q)] = -10
                else :
                    reward[(p,q)] = step_cost

        action = {(0, 0): {'D','R'},
        (0, 1):{'L','D','R'},
        (0, 2): {'L','D','R'},
        (0, 3): {'L','D','R'},
        (1, 0): {'U','R','D'},
        (1, 1): {'U','D','R','L'},
        (1, 2): {'U','D','R','L'},
        (1, 3): {'U','D','R','L'},
        (2, 0): {'U','R','D'},
        (2, 1): {'U','D','R','L'},
        (2, 2): {'U','D','R','L'},
        (2, 3): {'U','D','R','L'},
        (2, 4): {'D','U','L'},
        (3, 0): {'U','R','D'},
        (3, 1): {'U','D','R','L'},
        (3, 2): {'U','D','R','L'},
        (3, 3): {'U','D','R','L'},
        (3, 4): {'D','L','U'},
        (4, 0): {'U','R'},
        (4, 1): {'U','R','L'},
        (4, 2): {'U','R','L'},
        (4, 3): {'U','R','L'},
        (4, 4): {'U','L'},}

        prob = {(0, 0): {'D','R'},
        (0, 1):{'L','D','R'},
        (0, 2): {'L','D','R'},
        (0, 3): {'L','D','R'},
        (1, 0): {'U','R','D'},
        (1, 1): {'U','D','R','L'},
        (1, 2): {'U','D','R','L'},
        (1, 3): {'U','D','R','L'},
        (2, 0): {'U','R','D'},
        (2, 1): {'U','D','R','L'},
        (2, 2): {'U','D','R','L'},
        (2, 3): {'U','D','R','L'},
        (2, 4): {'D','U','L'},
        (3, 0): {'U','R','D'},
        (3, 1): {'U','D','R','L'},
        (3, 2): {'U','D','R','L'},
        (3, 3): {'U','D','R','L'},
        (3, 4): {'D','L','U'},
        (4, 0): {'U','R'},
        (4, 1): {'U','R','L'},
        (4, 2): {'U','R','L'},
        (4, 3): {'U','R','L'},
        (4, 4): {'U','L'},}

        prob = {}
        for i in action:
            for j in action[i]:
                d = np.random.randint(5)/10
                for k in action[i]:
                    if(j==k):
                        p = 1 - d
                    else:
                        p = d / (len(action[i])-1)
                    if (i[0],i[1],j) in prob :
                        prob[i[0],i[1],j][self.get_nextState(i[0],i[1],k)] = p
                    else:
                        prob[i[0],i[1],j] = {self.get_nextState(i[0],i[1],k):p}

        self.set(reward,action,prob)

    def set(self,reward, action, prob):
        self.reward = reward
        self.action = action
        self.prob = prob

    def get_nextState(self,si,sj,action):
        if action == "U":
            si -= 1
        elif action == "D":
            si += 1
        elif action == "R":
            sj += 1
        elif action == "D":
            sj -= 1
        return si,sj

    def get_reward(self,si,sj):
        return self.reward[(si,sj)]

    def move(self,action):
        self.i,self.j = self.get_nextState(self.i,self.j,action)
        return self.get_reward(self.i,self.j)
    
    def terminate(self):
        if (self.i,self.j) in self.action:
            return False
        return True
    
    def current_state(self):
        return self.i,self.j
    
    def is_terminal(self,i,j):
        if (i,j) in self.action:
            return False
        return True

In [5]:
g = GridWorld(0.1)

In [6]:
#transition and reward function of S' / s2
transition = {}
reward_s2 = {}

for i in range(g.row):
    for j in range(g.column):
        if(i,j) in g.action:
            for action in g.action[(i,j)]:
                for k in g.prob[i,j,action]:
                    transition[(i,j,action,k[0],k[1])]=g.prob[i,j,action][k]
                    reward_s2[(i,j,action,k[0],k[1])] = g.get_reward(k[0],k[1])



In [7]:
def set_policy():
        policy = {
        (0, 0): {'R':1},
        (0, 1):{'R':1},
        (0, 2): {'R':1},
        (0, 3): {'R':1},
        (1, 0): {'U':1},
        (1, 1): {'U':1},
        (1, 2): {'U':1},
        (1, 3): {'U':1},
        (2, 0): {'U':1},
        (2, 2): {'U':1},
        (2, 3): {'U':1},
        (2, 4): {'L':1},
        (3, 0): {'U':1},
        (3, 1): {'R':1},
        (3, 2): {'U':1},
        (3, 4): {'U':1},
        (4, 0): {'U':.5,'R':.5},
        (4, 1): {'U':1},
        (4, 2): {'U':1},
        (4, 3): {'L':1},
        (4, 4): {'L':1},
        (0, 4): {'D':1},
        (1,4) : {'U':1}}

        return policy

policy = set_policy()

In [8]:
#initiate Value
V = {}

for p in range(g.row):
    for q in range(g.column):
            V[(p,q)] = 0

delta = 0.00001
gamma = 0.9

In [9]:
#print value
def plot_value(V):
    print("Value")
    for i in range(g.row):
        print ("---"*7)
        print("|",end=" ")
        for j in range(g.column):
            print("%.2f|" %V[(i,j)],end=" ")
        print("")
    print ("---"*7)

In [10]:
#print policy

def print_policy(policy):
    print("POLICY")
    for i in range(g.row):
        print ("---"*7)
        print("|",end=" ")
        for j in range(g.column):
            if (i,j) in policy:
                print(policy[(i,j)],"|",end=" ")
            else:
                print(" ","|",end=" ")
        print("")
    print ("---"*7)

print_policy(policy)

POLICY
---------------------
| {'R': 1} | {'R': 1} | {'R': 1} | {'R': 1} | {'D': 1} | 
---------------------
| {'U': 1} | {'U': 1} | {'U': 1} | {'U': 1} | {'U': 1} | 
---------------------
| {'U': 1} |   | {'U': 1} | {'U': 1} | {'L': 1} | 
---------------------
| {'U': 1} | {'R': 1} | {'U': 1} |   | {'U': 1} | 
---------------------
| {'U': 0.5, 'R': 0.5} | {'U': 1} | {'U': 1} | {'L': 1} | {'L': 1} | 
---------------------


In [11]:
# Run the model

def policy_evaluation(policy,V):
    temp = {}
    iter = 0
    while True:
        diff = 0
        for si in range(g.row):
            for sj in range(g.column):
                if not g.is_terminal(si,sj):
                    temp = 0
                    for action in g.action[(si,sj)]:
                        s2i,s2j = g.get_nextState(si,sj,action)
                        pi = 0
                        if (si,sj) in policy:
                            pi =  policy[(si,sj)].get(action,0)
                        temp += pi * transition[(si,sj,action,s2i,s2j)]*(reward_s2[(si,sj,action,s2i,s2j)]+ gamma * V[(s2i,s2j)])
                    
                    diff = max(diff,np.abs(V[(si,sj)]-temp))
                    V[(si,sj)]=temp
        iter = iter+1
        # print("Itereation :", iter, "      Diff :",diff)
        # plot_value(V)
        if diff < delta:
            break

    return V
    

In [12]:
# Run the model

def policy_improvement(policy,V):
    temp_policy = {}
    for si in range(g.row):
        for sj in range(g.column):
            if not g.is_terminal(si,sj):
                temp = {}
                for action in g.action[(si,sj)]:
                    temp_v = 0
                    for s2i in range(g.row):
                        for s2j in range(g.column):
                            trs = transition[(si,sj,action,s2i,s2j)] if (si,sj,action,s2i,s2j) in transition else 0
                            rew = reward_s2[(si,sj,action,s2i,s2j)] if (si,sj,action,s2i,s2j) in reward_s2 else 0
                            temp_v += trs *(rew+ gamma * V[(s2i,s2j)])
                    temp[action] = temp_v
            val = max(temp.values())
            res = [key for key in temp if temp[key] == val] 
            temp_policy[(si,sj)] = {res[0]:1}
    policy = temp_policy
        

    return policy
    

In [13]:
policy= set_policy()
iter = 0
while True:
    iter += 1
    print("Iteration : ",iter)
    V = policy_evaluation(policy,V)
    plot_value(V)
    new_policy = policy_improvement(policy,V)
    if new_policy==policy:
        break
    policy = new_policy
    print_policy(policy)

print_policy(policy)


Iteration :  1
Value
---------------------
| 0.62| 0.58| 0.60| 1.00| 0.00| 
---------------------
| 0.66| 0.37| 0.58| 0.90| 0.00| 
---------------------
| 0.48| 0.00| 0.62| 0.55| 1.00| 
---------------------
| 0.43| 0.57| 0.59| 0.00| 1.00| 
---------------------
| 0.24| 0.55| 0.51| 0.13| 0.47| 
---------------------
POLICY
---------------------
| {'D': 1} | {'R': 1} | {'R': 1} | {'R': 1} | {'R': 1} | 
---------------------
| {'U': 1} | {'R': 1} | {'R': 1} | {'U': 1} | {'U': 1} | 
---------------------
| {'U': 1} | {'R': 1} | {'L': 1} | {'R': 1} | {'L': 1} | 
---------------------
| {'R': 1} | {'R': 1} | {'U': 1} | {'R': 1} | {'L': 1} | 
---------------------
| {'R': 1} | {'U': 1} | {'U': 1} | {'R': 1} | {'U': 1} | 
---------------------
Iteration :  2
Value
---------------------
| 0.22| 0.58| 0.60| 1.00| 0.00| 
---------------------
| 0.30| 0.67| 0.82| 0.90| 0.00| 
---------------------
| 0.26| 0.32| 0.29| 1.00| 1.00| 
---------------------
| 0.33| 0.35| 0.32| 0.90| 1.00| 
------------

KeyboardInterrupt: 